In [23]:
import tensorflow as tf
import keras
from keras.datasets import mnist
from keras.layers import Input,Dense,Reshape,Flatten,BatchNormalization,LeakyReLU
from keras.models import Sequential,Model
import matplotlib.pyplot as plt
import numpy as np

In [24]:
tf.config.list_physical_devices()

[PhysicalDevice(name='/physical_device:CPU:0', device_type='CPU'),
 PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]

In [25]:
keras.__version__

'2.15.0'

In [26]:
X,y=mnist.load_data()

In [27]:
image_rows=28
image_cols=28
channels=1
image_shape=(image_rows,image_cols,channels)

In [38]:
def build_generator():
    noise_shape=(100,)
    
    model=Sequential()
    model.add(Dense(256,activation=LeakyReLU(0.02),input_shape=noise_shape))
    model.add(BatchNormalization(momentum=0.8))
    model.add(Dense(512,activation=LeakyReLU(0.02)))
    model.add(BatchNormalization(momentum=0.8))
    model.add(Dense(1024,activation=LeakyReLU(0.02)))
    model.add(BatchNormalization(momentum=0.8))
    model.add(Dense(np.prod(image_shape),activation='tanh'))
    model.add(Reshape(image_shape))
    model.summary()
    
    noise=Input(shape=noise_shape)
    img=model(noise)
    return Model(noise,img)

In [39]:
def buid_discriminator():
    
    
    model=Sequential()
    model.add(Flatten(input_shape=image_shape))
    model.add(Dense(512,activation=LeakyReLU(0.02)))
    model.add(Dense(256,activation=LeakyReLU(0.02)))
    model.add(Dense(1,activation='sigmoid'))
    model.summary()
    
    img=Input(shape=image_shape)
    validity=model(img)
    return Model(img,validity)
        

In [46]:
def train(epochs,batch_size=128,save_interval=500):
    (X_train,_),(_,_)=mnist.load_data()
    
    X_train=(X_train.astype(np.float32)-127.5)/127.5
    X_train=np.expand_dims(X_train,axis=3)
    half_batch=int(batch_size/2)
    
    for epoch in range(epochs):
        idx=np.random.randint(0,X_train.shape[0],half_batch)
        imgs=X_train[idx]
        
        noise=np.random.normal(0,1,(half_batch,100))
        
        gen_imgs=generator.predict(noise)
        
        d_loss_real=discriminator.train_on_batch(imgs,np.ones((half_batch,1)))
        d_loss_fake=discriminator.train_on_batch(gen_imgs,np.zeros((half_batch,1)))
        d_loss=0.5*np.add(d_loss_fake,d_loss_real)
        
        
        noise=np.random.normal(0,1,(batch_size,100))
        
        valid_y=np.array([1]*batch_size)
        
        g_loss=combined.train_on_batch(noise,valid_y)
        
        
        print(epoch,d_loss[0],100*d_loss[1])
        
        if epoch%save_interval==0:
            save_imgs(epoch)
        
        
        

In [51]:
def save_imgs(epoch):
    r,c=5,5
    noise=np.random.normal(0,1,(r*c,100))
    gen_imags=generator.predict(noise)
    
    gen_imags=0.5*gen_imags+0.5
    
    fig,axs=plt.subplots(r,c)
    cnt=0
    for i in range(r):
        for j in range(c):
            axs[i,j].imshow(gen_imags[cnt,:,:,0],cmap='gray')
            axs[i,j].axis('off')
            cnt+=1
    fig.savefig('/home/nitish/Documents/yolo_images_generated/mnist_%d.png'% epoch)
    plt.close()

In [ ]:
discriminator=buid_discriminator()
discriminator.compile(loss='binary_crossentropy',optimizer='adam',metrics=['accuracy'])

generator=build_generator()
generator.compile(loss='binary_crossentropy',optimizer='adam')


z=Input(shape=(100,))
img=generator(z)


discriminator.trainable=False

valid=discriminator(img)

combined=Model(z,valid)
combined.compile(loss='binary_crossentropy',optimizer='adam')

train(epochs=100000,batch_size=32,save_interval=200)

generator.save('generator_model_test.h5')

Model: "sequential_16"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten_8 (Flatten)         (None, 784)               0         
                                                                 
 dense_46 (Dense)            (None, 512)               401920    
                                                                 
 dense_47 (Dense)            (None, 256)               131328    
                                                                 
 dense_48 (Dense)            (None, 1)                 257       
                                                                 
Total params: 533505 (2.04 MB)
Trainable params: 533505 (2.04 MB)
Non-trainable params: 0 (0.00 Byte)
_________________________________________________________________
Model: "sequential_17"
_________________________________________________________________
 Layer (type)                Output Shape              Param

66 0.013674986927071586 100.0
1/1 [==============================] - 0s 13ms/step
67 0.00819082441739738 100.0
1/1 [==============================] - 0s 12ms/step
68 0.019076984841376543 100.0
1/1 [==============================] - 0s 15ms/step
69 0.10998427867889404 96.875
1/1 [==============================] - 0s 12ms/step
70 0.010851534954781528 100.0
1/1 [==============================] - 0s 12ms/step
71 0.0035957600994152017 100.0
1/1 [==============================] - 0s 12ms/step
72 0.0025860976602416486 100.0
1/1 [==============================] - 0s 13ms/step
73 0.0048669802490621805 100.0
1/1 [==============================] - 0s 15ms/step
74 0.008467155508697033 100.0
1/1 [==============================] - 0s 15ms/step
75 0.03505009040236473 96.875
1/1 [==============================] - 0s 13ms/step
76 0.005912057094974443 100.0
1/1 [==============================] - 0s 15ms/step
77 0.0014660639280918986 100.0
1/1 [==============================] - 0s 13ms/step
78 0.00448244

1/1 [==============================] - 0s 13ms/step
166 0.1093548908829689 96.875
1/1 [==============================] - 0s 12ms/step
167 0.25838169796043076 87.5
1/1 [==============================] - 0s 12ms/step
168 0.0012937532155774534 100.0
1/1 [==============================] - 0s 12ms/step
169 0.5000977069139481 75.0
1/1 [==============================] - 0s 12ms/step
170 0.4228358144428057 81.25
1/1 [==============================] - 0s 12ms/step
171 0.0247338024128112 100.0
1/1 [==============================] - 0s 12ms/step
172 0.01912178882776061 100.0
1/1 [==============================] - 0s 12ms/step
173 0.12225028288958129 96.875
1/1 [==============================] - 0s 11ms/step
174 0.003368807374499738 100.0
1/1 [==============================] - 0s 11ms/step
175 0.1517561161890626 93.75
1/1 [==============================] - 0s 11ms/step
176 0.009330226574093103 100.0
1/1 [==============================] - 0s 12ms/step
177 0.009365493926452473 100.0
1/1 [===========

1/1 [==============================] - 0s 13ms/step
265 0.2541195899248123 87.5
1/1 [==============================] - 0s 12ms/step
266 0.12288543861359358 93.75
1/1 [==============================] - 0s 12ms/step
267 0.07885516271926463 96.875
1/1 [==============================] - 0s 12ms/step
268 0.0740750515833497 100.0
1/1 [==============================] - 0s 12ms/step
269 0.17346961796283722 93.75
1/1 [==============================] - 0s 12ms/step
270 0.2601694385521114 90.625
1/1 [==============================] - 0s 13ms/step
271 0.020363859366625547 100.0
1/1 [==============================] - 0s 14ms/step
272 0.029252523672766984 100.0
1/1 [==============================] - 0s 12ms/step
273 0.09653639048337936 96.875
1/1 [==============================] - 0s 14ms/step
274 0.03268035687506199 100.0
1/1 [==============================] - 0s 12ms/step
275 0.13084467826411128 93.75
1/1 [==============================] - 0s 12ms/step
276 0.051402303390204906 96.875
1/1 [========

1/1 [==============================] - 0s 13ms/step
365 0.0824537156149745 96.875
1/1 [==============================] - 0s 13ms/step
366 0.1011961717158556 93.75
1/1 [==============================] - 0s 12ms/step
367 0.10904264636337757 96.875
1/1 [==============================] - 0s 12ms/step
368 0.33085519820451736 84.375
1/1 [==============================] - 0s 14ms/step
369 0.2787635358981788 90.625
1/1 [==============================] - 0s 13ms/step
370 0.023138457909226418 100.0
1/1 [==============================] - 0s 13ms/step
371 0.42170944809913635 87.5
1/1 [==============================] - 0s 12ms/step
372 0.5433657821267843 75.0
1/1 [==============================] - 0s 13ms/step
373 0.011630653403699398 100.0
1/1 [==============================] - 0s 13ms/step
374 0.4544764272868633 75.0
1/1 [==============================] - 0s 12ms/step
375 0.08554789423942566 96.875
1/1 [==============================] - 0s 13ms/step
376 0.33587175654247403 87.5
1/1 [=============

...

74821 0.4906654804944992 84.375
1/1 [==============================] - 0s 14ms/step
74822 0.7277380228042603 56.25
1/1 [==============================] - 0s 13ms/step
74823 0.5613716542720795 78.125
1/1 [==============================] - 0s 13ms/step
74824 0.4869658797979355 78.125
1/1 [==============================] - 0s 14ms/step
74825 0.587756335735321 68.75
1/1 [==============================] - 0s 13ms/step
74826 0.6447340250015259 59.375
1/1 [==============================] - 0s 16ms/step
74827 0.6904909610748291 53.125
1/1 [==============================] - 0s 13ms/step
74828 0.8526478111743927 37.5
1/1 [==============================] - 0s 13ms/step
74829 0.72017502784729 53.125
1/1 [==============================] - 0s 13ms/step
74830 0.6014626622200012 59.375
1/1 [==============================] - 0s 13ms/step
74831 0.611577570438385 59.375
1/1 [==============================] - 0s 13ms/step
74832 0.6709329187870026 56.25
1/1 [==============================] - 0s 13ms/step
7

1/1 [==============================] - 0s 221ms/step
74920 0.6506442725658417 65.625
1/1 [==============================] - 0s 30ms/step
74921 0.6439879238605499 68.75
1/1 [==============================] - 0s 12ms/step
74922 0.7092319130897522 62.5
1/1 [==============================] - 0s 14ms/step
74923 0.581721156835556 62.5
1/1 [==============================] - 0s 129ms/step
74924 0.602513998746872 68.75
1/1 [==============================] - 0s 37ms/step
74925 0.551400437951088 75.0
1/1 [==============================] - 0s 102ms/step
74926 0.622281014919281 65.625
1/1 [==============================] - 0s 34ms/step
74927 0.7173924446105957 62.5
1/1 [==============================] - 0s 29ms/step
74928 0.6152816712856293 75.0
1/1 [==============================] - 0s 80ms/step
74929 0.6317705363035202 65.625
1/1 [==============================] - 0s 99ms/step
74930 0.5513839870691299 71.875
1/1 [==============================] - 0s 183ms/step
74931 0.685501366853714 50.0
1/1 [==

1/1 [==============================] - 0s 171ms/step
75018 0.6121195554733276 62.5
1/1 [==============================] - 0s 29ms/step
75019 0.6139274835586548 68.75
1/1 [==============================] - 0s 192ms/step
75020 0.6139336824417114 62.5
1/1 [==============================] - 0s 57ms/step
75021 0.6570989787578583 65.625
1/1 [==============================] - 0s 371ms/step
75022 0.6704559028148651 59.375
1/1 [==============================] - 0s 74ms/step
75023 0.5759437382221222 68.75
1/1 [==============================] - 0s 110ms/step
75024 0.8119468688964844 50.0
1/1 [==============================] - 0s 25ms/step
75025 0.7103185951709747 46.875
1/1 [==============================] - 0s 13ms/step
75026 0.6138943135738373 62.5
1/1 [==============================] - 0s 13ms/step
75027 0.6570738852024078 59.375
1/1 [==============================] - 0s 15ms/step
75028 0.7093088030815125 59.375
1/1 [==============================] - 0s 15ms/step
75029 0.7411613464355469 59.37

1/1 [==============================] - 0s 14ms/step
75116 0.6195491254329681 56.25
1/1 [==============================] - 0s 13ms/step
75117 0.5080800652503967 75.0
1/1 [==============================] - 0s 13ms/step
75118 0.618760496377945 65.625
1/1 [==============================] - 0s 13ms/step
75119 0.5062127113342285 78.125
1/1 [==============================] - 0s 14ms/step
75120 0.595754861831665 65.625
1/1 [==============================] - 0s 14ms/step
75121 0.6243955194950104 62.5
1/1 [==============================] - 0s 14ms/step
75122 0.5254656374454498 78.125
1/1 [==============================] - 0s 15ms/step
75123 0.569786787033081 65.625
1/1 [==============================] - 0s 13ms/step
75124 0.5372835844755173 71.875
1/1 [==============================] - 0s 12ms/step
75125 0.6886349320411682 59.375
1/1 [==============================] - 0s 13ms/step
75126 0.6624857783317566 62.5
1/1 [==============================] - 0s 14ms/step
75127 0.5769608616828918 78.125
1/

1/1 [==============================] - 0s 13ms/step
75214 0.6235157251358032 59.375
1/1 [==============================] - 0s 35ms/step
75215 0.5461625158786774 75.0
1/1 [==============================] - 0s 17ms/step
75216 0.5999629497528076 65.625
1/1 [==============================] - 0s 13ms/step
75217 0.6364200711250305 56.25
1/1 [==============================] - 0s 16ms/step
75218 0.5285258442163467 75.0
1/1 [==============================] - 0s 12ms/step
75219 0.6227976679801941 68.75
1/1 [==============================] - 0s 15ms/step
75220 0.5016334056854248 81.25
1/1 [==============================] - 0s 15ms/step
75221 0.6514995098114014 56.25
1/1 [==============================] - 0s 17ms/step
75222 0.5885040163993835 71.875
1/1 [==============================] - 0s 15ms/step
75223 0.4385076314210892 84.375
1/1 [==============================] - 0s 17ms/step
75224 0.6282812356948853 59.375
1/1 [==============================] - 0s 91ms/step
75225 0.5320831090211868 71.875
